# 哈哈哈哈，牛（奇）逼（葩）的R版本SEIR来啦

In [1]:
rm(list = ls())
options(warn = -1)
library("tidyverse")
source("learn_epimodel_helper.R") # seir helper functions

-- Attaching packages --------------------------------------- tidyverse 1.3.0 --

√ ggplot2 3.2.1     √ purrr   0.3.3
√ tibble  2.1.3     √ dplyr   0.8.3
√ tidyr   1.0.2     √ stringr 1.4.0
√ readr   1.3.1     √ forcats 0.4.0

-- Conflicts ------------------------------------------ tidyverse_conflicts() --
x dplyr::filter() masks stats::filter()
x dplyr::lag()    masks stats::lag()


Attaching package: 'data.table'


The following objects are masked from 'package:dplyr':

    between, first, last


The following object is masked from 'package:purrr':

    transpose


Loading required package: networkDynamic

Loading required package: network

network: Classes for Relational Data
Version 1.16.0 created on 2019-11-30.
copyright (c) 2005, Carter T. Butts, University of California-Irvine
                    Mark S. Handcock, University of California -- Los Angeles
                    David R. Hunter, Penn State University
                    Martina Morris, University of Washington
       

## Our definition of SEIR

In [2]:
SEIR <- function(t, t0, parms) {
  with(as.list(c(t0, parms)), {
    
    # Population size, which is changing because people dies
    num <- s.num + e.num + i.num + r.num
    
    # Effective contact rate and FOI from a rearrangement of Beta * c * D
    ce <- R0 / i.dur # the people amount one could spread to before he recovers, the speed is that divide by i.dur
    lambda <- ce * i.num/num # when people dies more the infection rate is higher
    
    dS <- -lambda*s.num
    dE <- lambda*s.num - (1/e.dur)*e.num
    dI <- (1/e.dur)*e.num - (1 - cfr)*(1/i.dur)*i.num - cfr*(1/i.dur)*i.num
    dR <- (1 - cfr)*(1/i.dur)*i.num 
    
    # Compartments and flows are part of the derivative vector
    # Other calculations to be output are outside the vector, but within the containing list
    list(c(dS, dE, dI, dR, 
           se.flow = lambda * s.num,
           ei.flow = (1/e.dur) * e.num,
           ir.flow = (1 - cfr)*(1/i.dur) * i.num,
           d.flow = cfr*(1/i.dur)*i.num),
         num = num,
         i.prev = i.num / num,
         ei.prev = (e.num + i.num)/num)
  })
}

e.dur = 5.2
i.dur = 2.3
cfr = 0.05

In [3]:
us_states_covid19_daily = read_csv("../testnum_data_0506.csv")
head(us_states_covid19_daily)

Parsed with column specification:
cols(
  .default = col_double(),
  state = col_character(),
  dataQualityGrade = col_character(),
  lastUpdateEt = col_character(),
  hash = col_character(),
  dateChecked = col_datetime(format = ""),
  fips = col_character()
)

See spec(...) for full column specifications.



date     state positive negative pending hospitalizedCurrently
1 20200506 AK      372     23283   NA         8                 
2 20200506 AL     8581    100935   NA        NA                 
3 20200506 AR     3568     55435   NA        69                 
4 20200506 AS        0        83   NA        NA                 
5 20200506 AZ     9707     82030   NA       754                 
6 20200506 CA    58815    750221   NA      4681                 
  hospitalizedCumulative inIcuCurrently inIcuCumulative onVentilatorCurrently
1   NA                     NA            NA              NA                  
2 1158                     NA           442              NA                  
3  453                     NA            NA              14                  
4   NA                     NA            NA              NA                  
5 1430                    286            NA             193                  
6   NA                   1415            NA              NA                  
  ... hospitalized total  totalTestResults posNeg fips deathIncrease
1 ...   NA          23655  23655            23655 02    1           
2 ... 1158         109516 109516           109516 01   27           
3 ...  453          59003  59003            59003 05    5           
4 ...   NA             83     83               83 60    0           
5 ... 1430          91737  91737            91737 04   31           
6 ...   NA         809036 809036           809036 06   95           
  hospitalizedIncrease negativeIncrease positiveIncrease
1  0                     962               1            
2 51                    2454             296            
3  0                    4296              72            
4  0                       0               0            
5 33                    3075             402            
6  0                   26531            2603            
  totalTestResultsIncrease
1   963                   
2  2750                   
3  4368                   
4     0                   
5  3477                   
6 29134

In [4]:
head(us_states_covid19_daily %>% filter(state == 'NY') %>% select(positive, recovered, death)) # cumulative

positive recovered death
1 321192   54597     19877
2 321192   58950     19645
3 318953   58950     19415
4 316415   58950     19189
5 312977   57540     18909
6 308314   56187     18610

In [5]:
us_states_covid19_daily = data.table(us_states_covid19_daily)
us_states_covid19_daily$date <- sapply(us_states_covid19_daily $date, function(x){
  paste(substring(x, 1, 4), substring(x, 5, 6), substring(x, 7, 8), sep="-")
})
us_states_covid19_daily[, date := as.Date(date)]
us_states_covid19_daily[is.na(recovered), recovered := 0]
us_states_covid19_daily[is.na(death), death := 0]
us_states_covid19_daily[, Infected := positive - recovered - death]#us_states_covid19_daily[, Infected := positive - recovered - death]
us_states_covid19_daily <- us_states_covid19_daily[, .(date, state, Infected)]
head(us_states_covid19_daily)

date       state Infected
1 2020-05-06 AK       78   
2 2020-05-06 AL     8241   
3 2020-05-06 AR     1374   
4 2020-05-06 AS        0   
5 2020-05-06 AZ     7588   
6 2020-05-06 CA    56403

In [6]:
us_states_covid19_latest <- us_states_covid19_daily[date == max(date)]
us_states_covid19_latest <- us_states_covid19_latest[order(-Infected)]
head(us_states_covid19_latest)

date       state Infected
1 2020-05-06 NY    246718  
2 2020-05-06 NJ    107699  
3 2020-05-06 MA     67605  
4 2020-05-06 IL     65258  
5 2020-05-06 CA     56403  
6 2020-05-06 PA     48739

In [7]:
top_10_states <- us_states_covid19_latest[1:10,]$state

us_states_covid19_daily_top10 <- us_states_covid19_daily[state %in% top_10_states, ]
us_states_covid19_daily_top10 <- us_states_covid19_daily_top10[Infected > 200, ]

options(repr.plot.width=15, repr.plot.height=10, repr.plot.res = 1000)

ggplot(us_states_covid19_daily_top10) +
  geom_line(aes(x=date, y=Infected)) +
  facet_wrap(~state, scales = 'free') +
  theme(text = element_text(size = 15), element_line(size = 1))

ggplot(us_states_covid19_daily_top10) +
  geom_line(aes(x=date, y=Infected)) +
  facet_wrap(~state) + 
  scale_y_continuous(trans = 'log10') + 
  theme(text = element_text(size = 15), element_line(size = 1))


In [8]:
all_states <- us_states_covid19_latest[Infected > 2000]$state
us_states_covid19_daily_all_states <- us_states_covid19_daily
us_states_covid19_daily_all_states <- us_states_covid19_daily_all_states[Infected > 200, ]

In [9]:
state_populations <- fread("state_populations_clean.csv")

In [10]:
if (!"state_report_list_all.rds" %in% dir()){
    state_report_list <- list()
    for (state_abbr in all_states){
      state_full_name <- state_populations[state == state_abbr]$state_full_name
      print(state_full_name)
      if(length(state_full_name) == 0){
        print(paste0(state_abbr, " is not found in the 50 states"))
        next
      }
      Infected_table_state <- us_states_covid19_daily_all_states[state == state_abbr]
      Infected_table_state <- Infected_table_state[order(date)]
      N <- state_populations[state == state_abbr]$population
      best_knots <- SEIR_US_fitting_three_period(Infected_table_state, N)

      state_report_list[[state_abbr]] <- report_fitted_result(best_knots, Infected_table_state, 
                                                              plot_title = paste0("State ", state_full_name),
                                                              plot.show.flag = F)
    }
    saveRDS(state_report_list, "state_report_list_all.rds")
}else{
    state_report_list <- readRDS("state_report_list_all.rds")
}


In [11]:
post_process = function(state_report_list){
    linear_daily_increase_vec <- c()
    first_expo_R0 <- c()
    second_expo_R0 <- c()
    knot1 <- c()
    knot2 <- c()
    loss_ <- c()
    for (state_abbr in all_states){
      linear_daily_increase <- state_report_list[[state_abbr]]$linear_daily_increase
      if(is.null(linear_daily_increase)){
        linear_daily_increase_vec <- c(linear_daily_increase_vec, NA)
      }else{
        linear_daily_increase_vec <- c(linear_daily_increase_vec, linear_daily_increase)
      }

      Opt1 <- state_report_list[[state_abbr]]$Opt1
      if(is.null(Opt1)){
        first_expo_R0 <- c(first_expo_R0, NA)
      }else{
        first_expo_R0 <- c(first_expo_R0, Opt1$par)
      }

      Opt2 <- state_report_list[[state_abbr]]$Opt2
      if(is.null(Opt2)){
        second_expo_R0 <- c(second_expo_R0, NA)
      }else{
        second_expo_R0 <- c(second_expo_R0, Opt2$par)
      }

      knot1 <- c(knot1, state_report_list[[state_abbr]]$knot1)
      knot2 <- c(knot2, state_report_list[[state_abbr]]$knot2)
      loss_ <- c(loss_, state_report_list[[state_abbr]]$loss)
    }

    state_report_df_tmp <- data.table(linear_daily_increase = linear_daily_increase_vec ,
                                      first_expo_R0 = first_expo_R0,
                                      second_expo_R0 = second_expo_R0,
                                      state = all_states,
                                      knot1 = knot1,
                                      knot2 = knot2,
                                      loss = loss_)

    state_report_df <- state_populations
    state_report_df <- merge(state_report_df, us_states_covid19_latest[,.(state, Infected)], by="state", all.x=T)
    state_report_df <- merge(state_report_df, state_report_df_tmp, by="state", all.x=T)

    state_min_date <- us_states_covid19_daily_all_states[,.(min_date = min(date)), by="state"]
    state_report_df <- merge(state_report_df, state_min_date, by="state")

    state_areas <- fread("state-areas.csv")
    colnames(state_areas) <- c("state_full_name", "area_sq_mile")

    state_report_df <- merge(state_report_df, state_areas, by="state_full_name")
    state_report_df[, pop_density := population/area_sq_mile]

    state_report_df[, knot1 := min_date + knot1]
    state_report_df[, knot2 := min_date + knot2]

    state_report_df <- within(state_report_df,{
      linear_daily_increase <- round(linear_daily_increase, 2)
      first_expo_R0 <- round(first_expo_R0, 2)
      second_expo_R0 <- round(second_expo_R0, 2)
    })

    state_report_df$first_expo_R0 <- NULL
    state_report_df$knot1 <- NULL
    current_date <- max(us_states_covid19_daily$date)
    state_report_df[, expo_days:= knot2 - min_date]
    state_report_df[, linear_days:= current_date  - knot2]
    state_report_df[is.na(knot2), expo_days := current_date  - min_date]
    state_report_df
}

In [12]:
state_report_df = post_process(state_report_list)

In [13]:
state_report_df[order(-second_expo_R0)]

state_full_name state population Infected linear_daily_increase
1  New York        NY    19862512   246718   5420.24              
2  New Jersey      NJ     9032872   107699   2692.31              
3  Connecticut     CT     3588683    23931    662.03              
4  Massachusetts   MA     6895917    67605   1590.01              
5  Pennsylvania    PA    12823989    48739   1259.76              
6  Indiana         IN     6699629    20493    465.84              
7  Michigan        MI     9991177    25145    557.43              
8  Louisiana       LA     4682509     7968   -548.69              
9  Florida         FL    21312211    36397    807.22              
10 Texas           TX    28704330    15852    242.39              
11 Colorado        CO     5684203    13660    304.47              
12 Georgia         GA    10545138    29385    707.17              
13 Tennessee       TN     6782564     7135    106.28              
14 California      CA    39776830    56403   1248.50              
15 Ohio            OH    11694664    20351    468.11              
16 Alabama         AL     4888949     8241    193.80              
17 Maryland        MD     6079602    24823    628.40              
18 Missouri        MO     6135888     8706    198.06              
19 Arizona         AZ     7123898     7588    147.85              
20 North Carolina  NC    10390149    12281    276.73              
21 Virginia        VA     8525660    16926    362.60              
22 Nevada          NV     3056824     5184    112.75              
23 Wisconsin       WI     5818049     4191     81.82              
24 Washington      WA     7530552    14732    254.72              
25 Rhode Island    RI     1061712     9170    291.82              
26 Illinois        IL    12768320    65258   1552.96              
27 Utah            UT     3159345     3028     37.65              
28 Mississippi     MS     2982785     3629    -55.80              
29 Kentucky        KY     4472265     3489     61.96              
30 Nebraska        NE     1932549     6356        NA              
31 Iowa            IA     3160553     6382        NA              
32 Kansas          KS     2918515     5272        NA              
33 South Carolina  SC     5088916     2815   -138.91              
34 Delaware        DE      971180     3577    112.40              
35 New Mexico      NM     2090708     3012        NA              
36 Minnesota       MN     5628162     3089        NA              
37 Arkansas        AR     3020327     1374        NA              
38 Hawaii          HI     1426393       57        NA              
39 Idaho           ID     1753860      683        NA              
40 Maine           ME     1341582      426        NA              
41 Montana         MT     1062330       23        NA              
42 New Hampshire   NH     1350575     1439        NA              
43 North Dakota    ND      755238      710        NA              
44 Oklahoma        OK     3940521     1039        NA              
45 Oregon          OR     4199563     1676        NA              
46 South Dakota    SD      877790      773        NA              
47 Vermont         VT      623960      150        NA              
48 West Virginia   WV     1803077      482        NA              
   second_expo_R0 knot2      loss       min_date   area_sq_mile pop_density
1  5.21           2020-03-27 1.32381340 2020-03-11  54475        364.617017
2  5.01           2020-03-30 1.00873826 2020-03-17   8722       1035.642284
3  4.34           2020-04-01 0.97137120 2020-03-22   5544        647.309343
4  3.99           2020-04-03 0.74467188 2020-03-19  10555        653.331786
5  3.91           2020-03-30 0.28143031 2020-03-20  46058        278.431304
6  3.69           2020-04-02 0.24296063 2020-03-23  36420        183.954668
7  3.41           2020-03-24 2.14865762 2020-03-09  96810        103.203977
8  3.24           2020-04-08 2.65440574 2020-03-18  51843         90.320950
9  3.15           2020-04-04 0.24903

## Visualization

In [14]:
state_report_df$linear_days = as.numeric(state_report_df$linear_days )
state_report_df$expo_days = as.numeric(state_report_df$expo_days)

In [15]:
library(leaflet)
US_map_visualization = function(state_info, varname){
  states <- geojsonio::geojson_read("us-states.geojson", what = "sp")
  states@data = states@data %>% left_join(state_info, by = c("name" = "state_full_name"))
  #bins <- c(0, 10, 20, 50, 100, 200, 500, 1000, Inf)
  pal <- colorBin("YlOrRd", domain = states[[varname]])
  
  labels <- sprintf(
    "<strong>%s</strong><br/>%s: %g",
    states$name, varname, states[[varname]]
  ) %>% lapply(htmltools::HTML)
  
  leaflet(states) %>%
    setView(-96, 37.8, 4) %>%
    addProviderTiles("MapBox", options = providerTileOptions(
      id = "mapbox.light",
      accessToken = Sys.getenv('MAPBOX_ACCESS_TOKEN'))) %>%
    addPolygons(
      fillColor = ~pal(get(varname)),
      weight = 2,
      opacity = 1,
      color = "white",
      dashArray = "3",
      fillOpacity = 0.7,
      highlight = highlightOptions(
        weight = 5,
        color = "#666",
        dashArray = "",
        fillOpacity = 0.7,
        bringToFront = TRUE),
      label = labels,
      labelOptions = labelOptions(
        style = list("font-weight" = "normal", padding = "3px 8px"),
        textsize = "15px",
        direction = "auto")) %>%
    addLegend(pal = pal, values = ~get(varname), opacity = 0.7, title = varname,
              position = "bottomright")
}

In [16]:
us_states_covid19_daily_plot = us_states_covid19_daily_all_states[order(state, date)] %>% 
    filter(state %in% all_states)
n = us_states_covid19_daily_plot %>% group_by(state) %>% summarize(n())
ypred = c()
for(c_state in sort(all_states)){
    temp = length(state_report_list[[c_state]]$y_prediction)
    if (temp == 0){
        us_states_covid19_daily_plot = us_states_covid19_daily_plot %>% filter(state != c_state)
        next
    }
    ypred = c(ypred, state_report_list[[c_state]]$y_prediction)
}
us_states_covid19_daily_plot$ypred = ypred
head(us_states_covid19_daily_plot)

date       state Infected ypred   
1 2020-03-24 AL    215      215.0000
2 2020-03-25 AL    283      299.4550
3 2020-03-26 AL    505      378.5249
4 2020-03-27 AL    584      463.5933
5 2020-03-28 AL    693      561.4467
6 2020-03-29 AL    802      677.1639

In [17]:
options(repr.plot.width=15, repr.plot.height=10, repr.plot.res = 1000)
us_states_covid19_daily_plot = us_states_covid19_daily_plot %>% filter(state %in% top_10_states)
ggplot(us_states_covid19_daily_plot) + 
      geom_line(aes(x = date, y = ypred)) +
      geom_point(aes(x=date, y=Infected)) +
      scale_y_continuous(trans = 'log10') +
      facet_wrap(".~state", scales = 'free') + 
      ggtitle("fit accuracy") +
      ylab("Current Infected Count") + 
      theme(text = element_text(size = 15), element_line(size = 0.8))

In [28]:
US_map_visualization(state_report_df, "second_expo_R0")

HTML widgets cannot be represented in plain text (need html)

In [19]:
US_map_visualization(state_report_df, "expo_days")

HTML widgets cannot be represented in plain text (need html)

## Compare to other methods (testset + calculate MSE)

In [20]:
us_states_covid19_daily_all_states_train = us_states_covid19_daily_all_states %>% filter(date < as.Date('2020-04-20'))
us_states_covid19_daily_all_states_test = us_states_covid19_daily_all_states %>% filter(date >= as.Date('2020-04-20'))
us_states_covid19_daily_all_states_train = data.table(us_states_covid19_daily_all_states_train)
us_states_covid19_daily_all_states_test = data.table(us_states_covid19_daily_all_states_test)

In [21]:
head(us_states_covid19_daily_all_states_train)
head(us_states_covid19_daily_all_states_test)

date       state Infected
1 2020-04-19 AL     4683   
2 2020-04-19 AR     1020   
3 2020-04-19 AZ     3751   
4 2020-04-19 CA    29167   
5 2020-04-19 CO     9022   
6 2020-04-19 CT    16464

date       state Infected
1 2020-05-06 AL     8241   
2 2020-05-06 AR     1374   
3 2020-05-06 AZ     7588   
4 2020-05-06 CA    56403   
5 2020-05-06 CO    13660   
6 2020-05-06 CT    23931

In [22]:
if (!"state_report_list_train.rds" %in% dir()){
    state_report_list <- list()
    for (state_abbr in all_states){
      state_full_name <- state_populations[state == state_abbr]$state_full_name
      print(state_full_name)
      if(length(state_full_name) == 0){
        print(paste0(state_abbr, " is not found in the 50 states"))
        next
      }
      Infected_table_state <- us_states_covid19_daily_all_states_train[state == state_abbr]
      Infected_table_state <- Infected_table_state[order(date)]
      N <- state_populations[state == state_abbr]$population
      best_knots <- SEIR_US_fitting_three_period(Infected_table_state, N)

      state_report_list_train[[state_abbr]] <- report_fitted_result(best_knots, Infected_table_state, 
                                                              plot_title = paste0("State ", state_full_name),
                                                              plot.show.flag = F)
    }
    saveRDS(state_report_list, "state_report_list_train.rds")
}else{
    state_report_list_train <- readRDS("state_report_list_train.rds")
}

In [23]:
head(us_states_covid19_daily_all_states_test[order(state, date)] %>% 
    filter(state %in% all_states) %>% group_by(state) %>% summarize(n()))

state n()
1 AL    17 
2 AZ    17 
3 CA    17 
4 CO    17 
5 CT    17 
6 DC    17

In [24]:
us_states_covid19_train_latest <- us_states_covid19_daily_all_states_train[date == max(date)]
head(us_states_covid19_train_latest)
us_states_covid19_daily_test = us_states_covid19_daily_all_states_test[order(state, date)] %>% 
    filter(state %in% all_states)
days = 1:17
ypred_total = c()
for(c_state in sort(all_states)){
    temp = as.numeric(state_report_list_train[[c_state]]$linear_daily_increase)
    print(c_state)
    print(temp)
    if (length(temp) == 0){
        us_states_covid19_daily_test = us_states_covid19_daily_test %>% filter(state != c_state)
        next
    }else{
        last = us_states_covid19_train_latest[state == c_state]$Infected
        ypred = last + temp * days
        ypred_total = c(ypred_total, ypred)
    }
}
us_states_covid19_daily_test$ypred = ypred_total

date       state Infected
1 2020-04-19 AL     4683   
2 2020-04-19 AR     1020   
3 2020-04-19 AZ     3751   
4 2020-04-19 CA    29167   
5 2020-04-19 CO     9022   
6 2020-04-19 CT    16464

[1] "AL"
[1] 191.5612
[1] "AZ"
[1] 142.7827
[1] "CA"
[1] 1099.234
[1] "CO"
[1] 334.7704
[1] "CT"
[1] 667.6856
[1] "DC"
numeric(0)
[1] "DE"
numeric(0)
[1] "FL"
[1] 1027.568
[1] "GA"
[1] 677.8765
[1] "IA"
numeric(0)
[1] "IL"
[1] 1088.117
[1] "IN"
[1] 415.5682
[1] "KS"
numeric(0)
[1] "KY"
numeric(0)
[1] "LA"
[1] 644.5558
[1] "MA"
[1] 1361.702
[1] "MD"
[1] 537.3533
[1] "MI"
[1] 752.4292
[1] "MN"
numeric(0)
[1] "MO"
[1] 212.0306
[1] "MS"
numeric(0)
[1] "NC"
[1] 246.6242
[1] "NE"
numeric(0)
[1] "NJ"
[1] 3037.043
[1] "NM"
numeric(0)
[1] "NV"
[1] 136.705
[1] "NY"
[1] 6618.156
[1] "OH"
[1] 365.0652
[1] "PA"
[1] 1359.207
[1] "RI"
numeric(0)
[1] "SC"
[1] -558.1716
[1] "TN"
[1] 62.27976
[1] "TX"
[1] 566.8592
[1] "UT"
[1] 59.61893
[1] "VA"
[1] 307.3655
[1] "WA"
[1] 329.3703
[1] "WI"
[1] 145.4414


In [25]:
options(repr.plot.width=15, repr.plot.height=10, repr.plot.res = 1000)
us_states_covid19_daily_test_top10 = us_states_covid19_daily_test %>% filter(state %in% top_10_states)
ggplot(us_states_covid19_daily_test_top10) + 
      geom_line(aes(x = date, y = ypred)) +
      geom_point(aes(x=date, y= Infected)) +
      scale_y_continuous(trans = 'log10') +
      facet_wrap(".~state", scales = 'free') + 
      ggtitle("True/Pred Infected Count on Test set") +
      ylab("True/Pred Infected Count") + 
      theme(text = element_text(size = 15), element_line(size = 0.8))


In [26]:
# calculate MSE
print(paste0("Total States: ", length(unique(us_states_covid19_daily_test$state))))
us_states_covid19_daily_test %>% group_by(state) %>% summarize(MSE = (mean((ypred - Infected)**2)))

[1] "Total States: 27"


state MSE         
1  AL    1.302260e+04
2  AZ    4.102208e+05
3  CA    2.514983e+07
4  CO    8.206153e+05
5  CT    6.457051e+06
6  FL    1.265685e+07
7  GA    7.292397e+04
8  IL    9.732880e+07
9  IN    2.299697e+06
10 LA    3.680005e+08
11 MA    2.733134e+07
12 MD    5.763450e+06
13 MI    5.828297e+07
14 MO    1.263144e+05
15 NC    9.873532e+05
16 NJ    2.226516e+08
17 NV    1.401008e+05
18 NY    1.055643e+09
19 OH    3.776859e+06
20 PA    7.345927e+06
21 SC    4.114021e+07
22 TN    2.407143e+06
23 TX    2.131045e+07
24 UT    7.383650e+04
25 VA    8.282089e+06
26 WA    2.364168e+06
27 WI    2.401705e+06

In [27]:
# overall MSE
mean((us_states_covid19_daily_test$ypred - us_states_covid19_daily_test$Infected)**2)

[1] 73082877